In [1]:
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plyfile import PlyData

In [2]:
def load_off_file(file_path):
    with open(file_path, 'r') as file:
        lines = file.readlines()

    # Extracting information from the OFF file
    num_vertices, num_faces, _ = map(int, lines[1].split())
    vertices = np.array([list(map(float, line.split()[0:3])) for line in lines[2:2+num_vertices]])

    # Assuming faces are triangles for simplicity
    faces = np.array([list(map(int, line.split()[1:])) for line in lines[2+num_vertices:]])

    return vertices, faces

In [3]:
def load_ply_file(file_path):
    # Load PLY file
    ply_data = PlyData.read(file_path)

    # Extract vertex data
    vertices = np.array([(vertex['x'], vertex['y'], vertex['z']) for vertex in ply_data['vertex']])

    # Extract face data
    faces = np.array([list(face) for face in ply_data['face']['vertex_indices']])

    return vertices, faces

In [4]:
# associate coord to label and plot colored labels
def load_txt_file(file_path):
    try:
        with open(file_path, 'r') as file:
            content = file.readlines()
            # Remove newline characters from each line
            content = [line.strip() for line in content]
        return content
    except FileNotFoundError:
        print(f"The file '{file_path}' was not found.")
        return None
    except Exception as e:
        print(f"An error occurred: {e}")
        return None

In [5]:
def read_obj_file(file_path):
    vertices = []
    faces = []

    with open(file_path, 'r') as obj_file:
        for line in obj_file:
            # Split the line into words
            words = line.split()

            if not words:
                continue

            # Check for vertex data
            if words[0] == 'v':
                vertex = list(map(float, words[1:]))
                vertices.append(vertex)

            # Check for face data
            elif words[0] == 'f':
                face = [int(vertex.split('/')[0]) for vertex in words[1:]]
                faces.append(face)

    return np.array(vertices), np.array(faces)

In [6]:
def show_3d_model(path_model, path_label):
    
    # Load models
    if path_model.endswith('ply'):
        vertices, faces = load_ply_file(path_model)
    elif path_model.endswith('off'):
        vertices, faces = load_off_file(path_model)
    elif path_model.endswith('obj'):
        vertices, faces = read_obj_file(path_model)

    # Load labels
    labels = load_txt_file(path_label)
    color_scale = {
    '1': 'red',
    '2': 'blue',
    '3': 'green',
    '4': 'yellow',
    '5': 'purple',
    '6': 'orange',
    '7': 'pink',
    '8': 'cyan'}
    face_colors = [color_scale[label] for row in labels for label in row]
    
    # Extract x, y, z coordinates from vertices
    x, y, z = vertices[:, 0], vertices[:, 1], vertices[:, 2]

    if path_model.endswith('obj'):
        # Create a 3D surface plot for faces
        mesh = go.Mesh3d(
            x=x,
            y=y,
            z=z,
            i=faces[:, 0]-1,
            j=faces[:, 1]-1,
            k=faces[:, 2]-1,
            opacity=1,
            # intensity=y,
            facecolor=face_colors,
            lighting=dict(ambient=0.8, diffuse=1, fresnel=0.2),
            colorscale='Viridis',
            )
    else:
        mesh = go.Mesh3d(
            x=x,
            y=y,
            z=z,
            i=faces[:, 0],
            j=faces[:, 1],
            k=faces[:, 2],
            opacity=1,
            # intensity=y,
            facecolor=face_colors,
            lighting=dict(ambient=0.8, diffuse=1, fresnel=0.2),
            colorscale='Viridis'
            )

    # Create a layout
    layout = go.Layout(
        scene=dict(
            aspectmode='data',
            camera=dict(eye=dict(x=1.25, y=1.25, z=1.25)),
            xaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            yaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            zaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            
        )
    )

    # Create a figure and add the scatter and surface plots
    fig = go.Figure(data=mesh, layout=layout)
    # fig = go.Figure(data=[scatter, mesh], layout=layout)

    fig.update_layout(width=800, height=600)
    
    # Show the figure
    fig.show()

In [7]:
# Plot train data
path = "/Users/adelemoreau/Desktop/MVA/S1/Geometric Data Analysis/Projet/diffusion-net/experiments/human_segmentation_original/data/sig17_seg_benchmark/"

# Adobe
path_model = path + "meshes/train/adobe/ToonFemaleA_tri_fixed.off"
path_label = path + "segs/train/adobe/ToonFemaleA_tri_fixed.txt"

# Faust
# path_model = path + "meshes/train/faust/tr_reg_023.ply"
# path_label = path + "segs/train/faust/faust_corrected.txt"

# MIT
# path_model = path + "meshes/train/MIT_animation/meshes_squat1/meshes/mesh_0160.obj"
# path_label = path + "segs/train/mit/mit_squat1_corrected.txt"

# Scape
# path_model = path + "meshes/train/scape/mesh015.off"
# path_label = path + "segs/train/scape/scape_corrected.txt"

show_3d_model(path_model, path_label)

In [8]:
# Plot test data
path = "/Users/adelemoreau/Desktop/MVA/S1/Geometric Data Analysis/Projet/diffusion-net/experiments/human_segmentation_original/data/sig17_seg_benchmark/"

# Schrec
input_nb = 17
path_model = path + f"meshes/test/shrec/{input_nb}.off"
path_label = path + f"segs/test/shrec/shrec_{input_nb}_full.txt"

show_3d_model(path_model, path_label)